In [12]:
# Instal ydata-profiling jika belum terpasang
!pip install ydata-profiling

In [13]:
# Impor pustaka yang diperlukan
import pandas as pd
import numpy as np
from ydata_profiling import ProfileReport

"""## 2. Memuat Data yang Belum Bersih (Unclean Data)

Kita akan memuat file `unclean_smartwatch_health_data.csv` ke dalam DataFrame pandas.
"""

# Muat dataset
file_path = 'unclean_smartwatch_health_data.csv'
df_unclean = pd.read_csv(file_path)

print("Data Awal (5 baris pertama):")
display(df_unclean.head())

print("\nInfo Data Awal:")
df_unclean.info()

"""## 3. Laporan Profiling Data SEBELUM Pembersihan

Sekarang, kita buat laporan kualitas data dari data asli yang belum dibersihkan. Laporan ini akan menunjukkan semua masalah seperti nilai yang hilang, tipe data yang salah, duplikat, dan outlier.
"""

# Import necessary libraries
from ydata_profiling import ProfileReport

# Generate the profile report
profile = ProfileReport(df_unclean, title="Profil laporan Analisis Kualitas Data Smartwatch (Unclean)")

# Display the report in the notebook
profile.to_notebook_iframe()

"""## 4. Proses Pembersihan Data

Berdasarkan temuan dari laporan di atas, kita akan melakukan beberapa langkah pembersihan.
"""

# Buat salinan dataframe agar data asli tetap utuh
df_clean = df_unclean.copy()

# --- LANGKAH 1: Mengatasi Nilai Teks yang Tidak Valid ('ERROR') ---
# Ganti nilai 'ERROR' di kolom 'Sleep Duration (hours)' dengan NaN (Not a Number)
df_clean['Sleep Duration (hours)'] = pd.to_numeric(df_clean['Sleep Duration (hours)'], errors='coerce')
print("Mengubah nilai 'ERROR' menjadi NaN selesai.")

# --- LANGKAH 2: Menghapus Baris dengan User ID yang Hilang ---
# Baris tanpa User ID tidak berguna, jadi kita hapus
initial_rows = len(df_clean)
df_clean.dropna(subset=['User ID'], inplace=True)
print(f"Menghapus {initial_rows - len(df_clean)} baris dengan User ID yang hilang.")

# --- LANGKAH 3: Menghapus Duplikat ---
initial_rows = len(df_clean)
df_clean.drop_duplicates(inplace=True)
print(f"Menghapus {initial_rows - len(df_clean)} baris duplikat.")


# --- LANGKAH 4: Mengisi Nilai yang Hilang (Imputation) ---
# Isi nilai numerik yang hilang dengan median kolomnya
numeric_cols = df_clean.select_dtypes(include=np.number).columns
for col in numeric_cols:
    median_val = df_clean[col].median()
    df_clean[col].fillna(median_val, inplace=True)
print("Mengisi nilai numerik yang hilang dengan median selesai.")

# --- LANGKAH 5: Memperbaiki Tipe Data ---
# Pastikan User ID adalah integer
df_clean['User ID'] = df_clean['User ID'].astype(int)
print("Memperbaiki tipe data User ID menjadi integer.")

# --- LANGKAH 6: Menstandarisasi Data Kategorikal ('Activity Level') ---
activity_mapping = {
    'Highly_Active': 'Highly Active',
    'Actve': 'Active'
}
df_clean['Activity Level'] = df_clean['Activity Level'].replace(activity_mapping)
# Ganti nilai yang tersisa yang tidak konsisten menjadi 'Unknown' atau modus
df_clean['Activity Level'].fillna('Unknown', inplace=True)
print("Menstandarisasi nilai pada kolom 'Activity Level' selesai.")


# --- LANGKAH 7: Mengatasi Outlier dan Nilai di Luar Rentang Valid ---
# Mengatasi Blood Oxygen Level > 100
df_clean['Blood Oxygen Level (%)'] = df_clean['Blood Oxygen Level (%)'].clip(lower=0, upper=100)
print("Membatasi 'Blood Oxygen Level (%)' pada rentang 0-100.")

# Menghapus outlier pada Heart Rate dan Step Count menggunakan metode IQR
for col in ['Heart Rate (BPM)', 'Step Count']:
    Q1 = df_clean[col].quantile(0.25)
    Q3 = df_clean[col].quantile(0.75)
    IQR = Q3 - Q1
    lower_bound = Q1 - 1.5 * IQR
    upper_bound = Q3 + 1.5 * IQR

    initial_rows = len(df_clean)
    df_clean = df_clean[(df_clean[col] >= lower_bound) & (df_clean[col] <= upper_bound)]
    print(f"Menghapus {initial_rows - len(df_clean)} outlier dari kolom '{col}'.")


# --- PEMBERSIHAN SELESAI ---
print("\nProses pembersihan data selesai!")
print("\nInfo Data SETELAH Pembersihan:")
df_clean.info()

print("\nData Bersih (5 baris pertama):")
display(df_clean.head())

"""## 5. Laporan Profiling Data SETELAH Pembersihan

Sekarang, kita akan membuat laporan kedua menggunakan data yang sudah bersih (`df_clean`). Bandingkan laporan ini dengan yang pertama untuk melihat peningkatannya.
"""

# Buat laporan dari dataframe yang sudah bersih
profile_clean = ProfileReport(df_clean, title="Laporan Kualitas Data - SETELAH Pembersihan")

# Simpan laporan sebagai file HTML
profile_clean.to_file("cleaned_data_report.html")

# Tampilkan laporan di dalam notebook
# profile_clean.to_widgets()

"""## 6. Kesimpulan

Dengan membandingkan dua laporan di atas (`unclean_data_report.html` dan `cleaned_data_report.html`), kita dapat melihat dengan jelas peningkatan kualitas data. Data yang bersih kini bebas dari nilai yang hilang, duplikat, outlier, dan inkonsistensi, sehingga siap untuk dianalisis lebih lanjut atau digunakan untuk pemodelan machine learning."""

Data Awal (5 baris pertama):


User ID  Heart Rate (BPM)  Blood Oxygen Level (%)    Step Count  \
0   4174.0         58.939776               98.809650   5450.390578   
1      NaN               NaN               98.532195    727.601610   
2   1860.0        247.803052               97.052954   2826.521994   
3   2294.0         40.000000               96.894213  13797.338044   
4   2130.0         61.950165               98.583797  15679.067648   

  Sleep Duration (hours) Activity Level Stress Level  
0      7.167235622316564  Highly Active            1  
1      6.538239375570314  Highly_Active            5  
2                  ERROR  Highly Active            5  
3      7.367789630207228          Actve            3  
4                    NaN  Highly_Active            6


Info Data Awal:
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 10000 entries, 0 to 9999
Data columns (total 7 columns):
 #   Column                  Non-Null Count  Dtype  
---  ------                  --------------  -----  
 0   User ID                 9799 non-null   float64
 1   Heart Rate (BPM)        9600 non-null   float64
 2   Blood Oxygen Level (%)  9700 non-null   float64
 3   Step Count              9900 non-null   float64
 4   Sleep Duration (hours)  9850 non-null   object 
 5   Activity Level          9800 non-null   object 
 6   Stress Level            9800 non-null   object 
dtypes: float64(4), object(3)
memory usage: 547.0+ KB


Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]


100%|██████████| 7/7 [00:00<00:00, 13.30it/s]


...


100%|██████████| 7/7 [00:00<00:00, 25.04it/s]


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

'## 6. Kesimpulan\n\nDengan membandingkan dua laporan di atas (`unclean_data_report.html` dan `cleaned_data_report.html`), kita dapat melihat dengan jelas peningkatan kualitas data. Data yang bersih kini bebas dari nilai yang hilang, duplikat, outlier, dan inkonsistensi, sehingga siap untuk dianalisis lebih lanjut atau digunakan untuk pemodelan machine learning.'

In [14]:
# Import necessary libraries
from ydata_profiling import ProfileReport

# Generate the profile report
profile = ProfileReport(df_clean, title="Profil laporan Analisis Kualitas Data Smartwatch")

# Display the report in the notebook
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]


100%|██████████| 7/7 [00:00<00:00, 18.26it/s]


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]